In [1]:
import xarray as xr
from tsai.all import *
import random
from scipy.spatial.distance import cdist
import dask
#import multiprocess as mp
import zarr
from numcodecs import Blosc

In [2]:
import torch
torch.cuda.device(0)
torch.cuda.is_available()

True

In [9]:
#TODO
#1. Done--Predict at level of granularity of snodas (elevation is the same as we've resampled it to be equivalent coords to snodas)
#   , choose those lat lons first
#   then pick the era5 lat lon matching 
#2. Done--Use a shorter time series (maybe 30-60 days; configurable) and expand the training set
# Compare 28 and longer sets
#3. Add in the gfs forecast for the gap between predicted date and era5 latency
#   (might need to move to a more recent era5 year)
#   3.a Finish downloadin the 2015 and 2016 data
#   STill need to download the accumulation data & convert 2016 data to nc
#   3.b map the variables between era5 and gfs
#   3.c update the script to add gfs for the last n days where n is the latency of era5
#4. Done--Test the full 2010 year and split it 
#5. Predict all snodas variables and create evaluation mechanism
#6. Done--Add all dates in and create model
#7. add aspect and angle data
#8. Investigate hourly era5 data
#short to long name lookup
#9. Done--Plot on graph and line
#10. Write the sample generator so it can be restarted (export the remaining lat/lon and provide as a parameters)
#11. Done--find the best model
#12. Explore which time series length is best
#13. Train with all data

In [10]:
#from concurrent.futures import ThreadPoolExecutor
#dask.config.set(pool=ThreadPoolExecutor(12))

In [3]:
base_path = 'D:/OAPMLData/6.SnowModelData/'
#//openmediavault/DataCold/SnowData

In [4]:
era5_ds = xr.open_zarr(base_path + '/era5_snodas/era5_tmp_daily2.zarr')
elevation_ds = xr.open_zarr(base_path + '/era5_snodas/elevation.zarr')
snow_ds = xr.open_zarr(base_path + '/era5_snodas/snodas.zarr')

In [17]:
era5_ds.chunks

Frozen({'time': (1096,), 'lat': (137,), 'lon': (274,)})

In [ ]:
#print out all the long names of the variables
i = 0
for k in era5_ds.keys():
    print(str(i) + ': ' + k + ' ' + era5_ds[k].long_name)
    i = i + 1

In [5]:
target_labels = ['BlowingSnowSublimation',
                    'NonSnowPrecip',
                    'SWE',
                    'SnowDepth',
                    'SnowMelt',
                    'SnowPrecip',
                    'SnowpackAvgTemp',
                    'SnowpackSublimation']

# Create the X set

In [6]:
def create_snow_mask(snow):
    mean_swe = snow.SWE.resample(time='1Y').mean()
    snow_mask = mean_swe.values >= 0
    return snow_mask

In [ ]:
def test_create_snow_mask():
    sm = create_snow_mask(snow_ds)
    i, j, k = np.where(sm == True)
    for t in range(len(j))[:100]:
        v = snow_ds.isel(lat=j[t], lon=k[t]).SWE.resample(time='1Y').mean().values[0]
        assert v != -9999, 'Sample lat index: ' + str(j[t]) + ' lon index: ' + str(k[t]) + ' has empty SWE'
test_create_snow_mask()    
    

In [7]:
def create_lat_lon_pairs(elevation, snow, era5):
    #get all the lat/lon pairs in elevation dataset.  Elevation dataset has been preprocessed to 
    #algin to era5 grid
    lats = elevation.lat.compute().values
    lons = elevation.lon.compute().values
    #compute only over lat/lon pairs over land and not exactly sealevel (heuristic for over-sea valid-values)
    #not_sealevel = (elevation['elevation']!=0).values == True
    snow_mask = create_snow_mask(snow) 
    mask = snow_mask #np.logical_and(elevation['elevation'].notnull().compute().values, not_sealevel, snow_mask)

    lat_lon_pairs = [(lats[i_lat],lons[i_lon]) for i_lat in range(len(lats)) for i_lon in range(len(lons)) if mask[0,i_lat,i_lon]]

    #get all the era5 lat/lon pairs
    era_lats = era5.lat.compute().values
    era_lons = era5.lon.compute().values
    era_lat_lon_pairs = [(lat,lon) for lat in era_lats for lon in era_lons]
    return lat_lon_pairs, era_lat_lon_pairs

In [8]:
#ele, era= create_lat_lon_pairs(elevation_ds, snow_ds, era5_ds)

In [ ]:
len(era)

In [ ]:
len(ele)

In [ ]:
def test_create_lat_lon_pairs_SWE():
    a, b = create_lat_lon_pairs(elevation_ds, snow_ds, era5_ds)
    for i in a[:10]:
        v = snow_ds.sel(lat=i[0], lon=i[1]).SWE.resample(time='1Y').mean().values[0] 
        #print(v)
        assert v != -9999.0, 'Sample lat: ' + str(i[0]) + ' lon: ' + str(i[1]) + ' has empty SWE'
test_create_lat_lon_pairs_SWE()

In [8]:

def write_batches(zarr_arr, zarr_y, input_data_series_len, X_series_len, X, y, X_size=64, first=0, last=64):
    start = random.sample(range(1,X_series_len+1), 1)[0]
    for s in range(start, input_data_series_len, X_series_len):
        if input_data_series_len - s < X_series_len:
            break
        
        print('expanding series ' + str(s) + ' ' + str(X_series_len) + ' ' + str(first) + ' ' + str(last))
        #catch exception ValueError if we run out of space (finiky about the last batch since we start in a random spot)
        try:
            zarr_arr[first : last] = X[:,:, s : s + X_series_len]
            zarr_y[first : last] = y[:,:, s + X_series_len - 2]
        except ValueError:
            break
        first = last
        last += X_size

In [9]:
from joblib import Parallel, delayed

In [72]:
def write_batches_parallel(zarr_arr, zarr_y, input_data_series_len, X_series_len, X, y, batch_number, X_size=64, write_start=0):#, first=0, last=64):    
    start = random.sample(range(1,X_series_len+1), 1)[0]
    sliding_window_factor = int((input_data_series_len / X_series_len)-1)
    def write_batch(s, b_number):
        if input_data_series_len - s < X_series_len:
            return -1
        first = write_start + (int(s/X_series_len) * X_size) #need to figure out which batch this is in the series
        last = first + X_size
        print('expanding series ' + str(s) + ' ' + str(X_series_len) + ' ' + str(first) + ' ' + str(last))
        try:
            zarr_arr[first : last] = X[:,:, s : s + X_series_len]
            zarr_y[first : last] = y[:,:, s + X_series_len - 2]
        except ValueError:
            return -1
        return last
    indexes = [s for s in range(start, input_data_series_len, X_series_len)]
    func = partial(write_batch, b_number=batch_number)
    last_indexes = Parallel(n_jobs=-1)(map(delayed(func), indexes))
    return max(last_indexes)

In [77]:
def create_dataset(era5, elevation, snow, X_size=64, X_series_len=28, num_batches=32, suffix='train'):
    #Open the output files

    input_data_series_len = era5.time.size
    num_vars = 440 #TODO: len(era5.data_vars) - len(target_labels)--this isnt' coorrect as we need to also add in lat,lon, elevation
    sliding_window_factor = int((input_data_series_len / X_series_len)-1)
    output_shape = (X_size*num_batches*(sliding_window_factor), num_vars, X_series_len) 
    print('Output shape: ' + str(output_shape))
    
    zarr_arr = zarr.open(base_path + '/X_merged_' + suffix + '.zarr', 
                         mode='w', shape=output_shape, dtype=np.float32,
                         compressor=Blosc(cname='zstd', clevel=9, shuffle=Blosc.SHUFFLE), 
                         synchronizer=zarr.ProcessSynchronizer('./x_semiphore.sync'))
    zarr_y = zarr.open(base_path + '/y_merged_' + suffix + '.zarr', 
                         mode='w', shape=(output_shape[0], len(target_labels)), dtype=np.float32, 
                         synchronizer=zarr.ProcessSynchronizer('./x_semiphore.sync'))
    
    
    lat_lon_pairs, era_lat_lon_pairs = create_lat_lon_pairs(elevation, snow, era5)
    y_final = []
    labels_final = []
    labels = None
    #first = 0
    #last = first + X_size
    write_index = 0
    for i in range(num_batches):
        #get a random selection from the elevation lat/lon pairs
        lat_lon_sample = random.sample(lat_lon_pairs, X_size)
        lat_lon_sample.sort(key=lambda x: str(x[0]) + '_' + str(x[1]))
        #find the era5 lat/lon pairs which are closest
        #due to preprocessing in elevation these are expected to be identical
        #this logic is useful though if that preprocessing wasn't done
        #TODO: only use matching logic when the datasets don't already match
        tree = cdist(era_lat_lon_pairs, lat_lon_sample).argmin(axis=0)
        nearest_era_lat_lon = [era_lat_lon_pairs[i] for i in tree]

        nearest_era_lat_lon.sort(key=lambda x: str(x[0]) + '_' + str(x[1]))

        #get the era5 data
        lat_z = xr.DataArray([t[0] for t in nearest_era_lat_lon], dims='z')
        lon_z = xr.DataArray([t[1] for t in nearest_era_lat_lon], dims='z')
        #pointwise select using new dim z
        era5_sample = era5.sel(lat=lat_z, lon=lon_z)

        #get the snow data--the data we want to predict for the same sample lat/lons
        #this was also preprocessed to match the grid
        snow_tmp = snow.sel(lat=lat_z, lon=lon_z, method='nearest')
        #overwrite the coordinates to be aligned with era5 to enable the merge
        snow_tmp.coords['lon'] = era5_sample.z.lon
        snow_tmp.coords['lat'] = era5_sample.z.lat
        
        X_da = xr.merge([era5_sample, snow_tmp])
        
        lat_lons = list(zip(X_da['lat'].values, X_da['lon'].values))

        #convert to numpy, this takes awhile
        X = X_da.to_array().values

        #convert the elevation set to daily as it comes in hourly
        elevation_tmp = elevation.sel(lat=lat_z, lon=lon_z, method='nearest').resample(time='1D').mean()
        elevation_tmp.coords['lat'] = era5_sample.z.lon
        elevation_tmp.coords['lon'] = era5_sample.z.lat

        np_elevation = elevation_tmp.to_array().values.reshape((1,input_data_series_len,X_size))

        times = era5_sample.time.compute()

        #crate new lat/lon variables for the training set
        lat_vars = [[x[0] for y in range(len(times))] for x in lat_lons] 
        lon_vars = [[x[1] for y in range(len(times))] for x in lat_lons] 

        X = np.append(X, np.array(lat_vars).T[np.newaxis, :], axis=0)
        X = np.append(X, np.array(lon_vars).T[np.newaxis, :], axis=0)

        #create new elevation variable for the training set
        X = np.append(X, np_elevation, axis=0)

        #create new day of year variable for the training set
        dayofyear_vars = [[x for x in X_da.time.dt.dayofyear.values] for x in range(X_size)]

        X = np.append(X, np.array(dayofyear_vars).T[np.newaxis, :], axis=0)
        #make it samples, vars, seq length
        X = np.moveaxis(X, [0,1,2], [1,2,0])

        #store the lables
        labels = list(X_da.data_vars)
        labels.extend(['lat', 'lon', 'elevation', 'dayofyear'])
        
        #split x & y
        target_indexes = [i for i, x in enumerate(labels) if x in target_labels]
        y = X[:,target_indexes,:]
        X = np.delete(X, target_indexes, axis=1)
        
        #only store labels on the first batch
        if labels is None:
            labels = [i for j, i in enumerate(labels) if j not in target_indexes]
        
        #store X & y
        write_index = write_batches_parallel(zarr_arr, zarr_y, input_data_series_len, X_series_len, X, y, i, write_start=write_index)
        #pick a random start date
        #start = random.sample(range(1,X_series_len+1), 1)[0]
        #test
        #return zarr_arr, zarr_y, start, input_data_series_len, X_series_len, X, y
        #for s in range(start, input_data_series_len, X_series_len):
        #    if input_data_series_len - s < X_series_len:
        #        break
        #    
        #    print('expanding series ' + str(s) + ' ' + str(X_series_len) + ' ' + str(first) + ' ' + str(last))
        #    #catch exception ValueError if we run out of space (finiky about the last batch since we start in a random spot)
        #    try:
        #        zarr_arr[first : last] = X[:,:, s : s + X_series_len]
        #        zarr_y[first : last] = y[:,:, s + X_series_len - 2]
        #    except ValueError:
        #        break
        #    first = last
        #    last += X_size
        #remove the sample so we don't duplicate
        [x for x in lat_lon_pairs if x not in lat_lon_sample]
    pd.Series(labels).to_csv(base_path + 'labels.csv', index=False)
    return zarr_arr, zarr_y, labels


In [62]:
#smaller dataset for testing
era5_ds_train = era5_ds.sel(time=slice('2010-01-01', '2010-03-31'))
elevation_ds_train = elevation_ds.sel(time=slice('2010-01-01', '2010-03-31'))
snow_ds_train = snow_ds.sel(time=slice('2010-01-01', '2010-03-31'))

In [75]:
#filter to just train dates between 2010-01-01 and 2012-01-01
era5_ds_train = era5_ds.sel(time=slice('2010-01-01', '2011-12-31'))
elevation_ds_train = elevation_ds.sel(time=slice('2010-01-01', '2011-12-31'))
snow_ds_train = snow_ds.sel(time=slice('2010-01-01', '2011-12-31'))


era5_ds_test = era5_ds.sel(time=slice('2012-01-01', '2012-12-31'))
elevation_ds_test = elevation_ds.sel(time=slice('2012-01-01', '2012-12-31'))
snow_ds_test = snow_ds.sel(time=slice('2012-01-01', '2012-12-31'))

In [78]:
%%time 
#2 chunks 3gb all threads no compressin
#CPU times: total: 7min 59s
#Wall time: 7min 37s

#2 chunks 2.9gb all threads .5 compression
#CPU times: total: 7min 25s
#Wall time: 8min 36s

#2 chunks 2gb all threads .9 compression
#CPU times: total: 26min 44s
#Wall time: 13min 52s
#8 threads
#CPU times: total: 28min 25s
#Wall time: 11min 59s
#4 threads
#CPU times: total: 30min 15s
#Wall time: 13min 29s
#12 threads
#CPU times: total: 26min 3s
#Wall time: 11min 25s

#new logic 2 chunks 12 threas
#CPU times: total: 27min 28s
#Wall time: 18min 41s
zarr_arr, zarr_y, labels = create_dataset(era5_ds_train, elevation_ds_train, snow_ds_train, X_size=64, num_batches=60, suffix='train')
#zarr_ds_X, zarr_ds_y, labels_1 = create_dataset(era5_ds_train, elevation_ds_train, snow_ds_train, X_size=64, num_batches=60, suffix='train')

Output shape: (96000, 440, 28)
CPU times: total: 17h 29min 45s
Wall time: 3h 30min 47s


In [79]:
zarr_ds_X_test, zarr_ds_y_test, labels_1_test = create_dataset(era5_ds_test, elevation_ds_test, snow_ds_test, X_size=64, num_batches=15, suffix='test')

Output shape: (11520, 440, 28)


In [6]:
#generate a test set of one date but all lat/lon variables
date = '2012-02-01'
num_days = 28
#select the date rage from date-numdays to date
date_range = pd.date_range(np.datetime64(date) - num_days, np.datetime64(date))
era5_ds_test = era5_ds.sel(time=date_range)
era5_ds_test

<xarray.Dataset>
Dimensions:          (time: 29, lat: 137, lon: 274)
Coordinates:
  * lat              (lat) float32 58.1 57.85 57.6 57.35 ... 24.6 24.35 24.1
  * lon              (lon) float32 -130.5 -130.3 -130.0 ... -62.79 -62.54 -62.29
  * time             (time) datetime64[ns] 2012-01-04 2012-01-05 ... 2012-02-01
Data variables: (12/436)
    alnid_max        (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_mean       (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_min        (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_sum        (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnip_max        (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnip_mean       (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    ...               ...
    z_min            (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    z_sum            (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    zust_max         (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    zust_mean        (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    zust_min         (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    zust_sum         (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
Attributes:
    Conventions:  CF-1.6
    history:      2023-01-30 01:04:22 GMT by grib_to_netcdf-2.25.1: /opt/ecmw...

In [7]:
lat_z = xr.DataArray(era5_ds_test.lat.values, dims='z')
lon_z = xr.DataArray(era5_ds_test.lon.values, dims='z1')
#pointwise select using new dim z
snow_ds_sample = snow_ds.sel(lat=lat_z, lon=lon_z, time=date_range, method='nearest')

In [8]:
snow_ds_sample

<xarray.Dataset>
Dimensions:                 (time: 29, z: 137, z1: 274)
Coordinates:
    lat                     (z) float64 58.1 57.85 57.6 ... 24.6 24.35 24.1
    lon                     (z1) float64 -130.5 -130.3 -130.0 ... -62.54 -62.29
  * time                    (time) datetime64[ns] 2012-01-04 ... 2012-02-01
Dimensions without coordinates: z, z1
Data variables:
    BlowingSnowSublimation  (time, z, z1) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    NonSnowPrecip           (time, z, z1) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SWE                     (time, z, z1) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowDepth               (time, z, z1) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowMelt                (time, z, z1) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowPrecip              (time, z, z1) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowpackAvgTemp         (time, z, z1) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowpackSublimation     (time, z, z1) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
Attributes:
    Conventions:  CF-1.5
    GDAL:         GDAL 2.3.2, released 2018/09/21
    history:      Sat Apr 22 11:26:31 2023: GDAL CreateCopy( ./2010/01_Jan//z...

In [9]:
#rename the coords to match era5
snow_ds_sample = snow_ds_sample.rename({'z':'lat', 'z1':'lon'})
snow_ds_sample

<xarray.Dataset>
Dimensions:                 (time: 29, lat: 137, lon: 274)
Coordinates:
    lat                     (lat) float64 58.1 57.85 57.6 ... 24.6 24.35 24.1
    lon                     (lon) float64 -130.5 -130.3 -130.0 ... -62.54 -62.29
  * time                    (time) datetime64[ns] 2012-01-04 ... 2012-02-01
Data variables:
    BlowingSnowSublimation  (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    NonSnowPrecip           (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SWE                     (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowDepth               (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowMelt                (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowPrecip              (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowpackAvgTemp         (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowpackSublimation     (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
Attributes:
    Conventions:  CF-1.5
    GDAL:         GDAL 2.3.2, released 2018/09/21
    history:      Sat Apr 22 11:26:31 2023: GDAL CreateCopy( ./2010/01_Jan//z...

In [10]:
#there is a duplicate snow timestamp, overwrite it
snow_ds_sample.coords['time'] = era5_ds_test.time
snow_ds_sample.coords['lat'] = era5_ds_test.lat
snow_ds_sample.coords['lon'] = era5_ds_test.lon

In [11]:
#join snow and era5 on lat and lon
X_da = xr.merge([era5_ds_test, snow_ds_sample])
X_da

<xarray.Dataset>
Dimensions:                 (time: 29, lat: 137, lon: 274)
Coordinates:
  * lat                     (lat) float32 58.1 57.85 57.6 ... 24.6 24.35 24.1
  * lon                     (lon) float32 -130.5 -130.3 -130.0 ... -62.54 -62.29
  * time                    (time) datetime64[ns] 2012-01-04 ... 2012-02-01
Data variables: (12/444)
    alnid_max               (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_mean              (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_min               (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_sum               (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnip_max               (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnip_mean              (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    ...                      ...
    SWE                     (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowDepth               (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowMelt                (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowPrecip              (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowpackAvgTemp         (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowpackSublimation     (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
Attributes:
    Conventions:  CF-1.6
    history:      2023-01-30 01:04:22 GMT by grib_to_netcdf-2.25.1: /opt/ecmw...

In [12]:
elevation_tmp = elevation_ds.sel(lat=lat_z, lon=lon_z, method='nearest').resample(time='1D').mean().sel(time=date_range)
elevation_tmp = elevation_tmp.rename({'z':'lat', 'z1':'lon'})

In [13]:
#merge X_da and elevation
X_da = xr.merge([X_da, elevation_tmp])
X_da

<xarray.Dataset>
Dimensions:                 (time: 29, lat: 137, lon: 274, band: 1)
Coordinates:
  * lat                     (lat) float32 58.1 57.85 57.6 ... 24.6 24.35 24.1
  * lon                     (lon) float32 -130.5 -130.3 -130.0 ... -62.54 -62.29
  * time                    (time) datetime64[ns] 2012-01-04 ... 2012-02-01
Dimensions without coordinates: band
Data variables: (12/445)
    alnid_max               (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_mean              (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_min               (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnid_sum               (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnip_max               (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    alnip_mean              (time, lat, lon) float32 dask.array<chunksize=(29, 137, 274), meta=np.ndarray>
    ...                      ...
    SnowDepth               (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowMelt                (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowPrecip              (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowpackAvgTemp         (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    SnowpackSublimation     (time, lat, lon) float32 dask.array<chunksize=(29, 3, 17), meta=np.ndarray>
    elevation               (time, band, lat, lon) float64 dask.array<chunksize=(1, 1, 137, 274), meta=np.ndarray>
Attributes:
    Conventions:  CF-1.6
    history:      2023-01-30 01:04:22 GMT by grib_to_netcdf-2.25.1: /opt/ecmw...

In [14]:
#stack the lat and lon dimensions
#takes about an 28min to run
X = X_da.to_array().stack(lat_lon=('lat', 'lon')).values

In [15]:
X.shape

(445, 29, 1, 37538)

In [16]:
X = X.reshape((445,29,37538))

In [17]:
X.shape

(445, 29, 37538)

In [18]:
X = np.moveaxis(X, [0,1,2], [1,2,0])

In [19]:
X.shape

(37538, 445, 29)

In [66]:
#add lat and lon as variables
lat_vars = np.array([[x for y in range(len(X_da.time))] for x in X_da.lat.values])
lon_vars = np.array([[x for y in range(len(X_da.time))] for x in X_da.lon.values])

In [73]:
stack_lat_lon = X_da.stack(lat_lon=('lat', 'lon')).lat_lon.values

In [77]:
lat_vars = [x[0] for x in stack_lat_lon]
lon_vars = [x[1] for x in stack_lat_lon]

In [78]:
#expand the array to two dimensions where the second dimension is all duplicates
lat_vars = np.array([[x for y in range(len(X_da.time))] for x in lat_vars])
lon_vars = np.array([[x for y in range(len(X_da.time))] for x in lon_vars])

In [80]:
np.array(lon_vars).shape

(37538, 29)

In [63]:
X.shape

(37538, 445, 29)

In [81]:
#insert in second to last row of second dimension; elevation needs to go last
X = np.insert(X, X.shape[1]-1, lat_vars, axis=1)
X = np.insert(X, X.shape[1]-1, lon_vars, axis=1)
#np.append(X, lat_vars[:,np.newaxis,:], axis=1).shape

In [96]:
X.shape

(37538, 447, 29)

In [102]:
#expand time values to be three dimensions and have lenge matching the first dimension of X
times = np.array([X_da.time.dt.dayofyear.values for x in range(X.shape[0])])

In [103]:
times[:,np.newaxis,:].shape

(37538, 1, 29)

In [106]:
X = np.append(X, times[:,np.newaxis,:], axis=1)

In [114]:
labels = list(X_da.data_vars)
labels.extend(['lat', 'lon', 'elevation', 'dayofyear'])

In [115]:
#split x & y
target_indexes = [i for i, x in enumerate(labels) if x in target_labels]
y = X[:,target_indexes,:]
X = np.delete(X, target_indexes, axis=1)

In [116]:
X.shape

(37538, 440, 29)

In [118]:
#output X to disk as numpy array
np.save('//openmediavault/DataCold/' + 'X_test_2012-02-01.npy', X[:,:,1:29])

In [119]:
y.shape

(37538, 8, 29)

In [120]:
np.save('//openmediavault/DataCold/' + 'y_test_2012-02-01.npy', y[:,:,-1])

In [122]:
#open X
pd.Series(labels).to_csv('//openmediavault/DataCold/labels.csv')

In [130]:
#split lat/lon into two columns
pd.DataFrame.from_records(X_da.stack(lat_lon=('lat','lon')).lat_lon.values).to_csv('//openmediavault/DataCold/lat_lon.csv', index=False)